### Beschaffung der Märchen

In [1]:
from os import sep
import requests
#from bs4 import BeautifulSoup
import pandas as pd
import gensim
from gensim.models.doc2vec import Doc2Vec, TaggedDocument
import json
from nltk.corpus import stopwords
from nltk.tokenize import word_tokenize
import multiprocessing
import numpy as np
#from sklearn.feature_extraction.text import TfidfVectorizer



In [2]:
result = requests.get("https://www.grimmstories.com/de/grimm_maerchen/list")
result.status_code

200

In [3]:
src = result.content
soup = BeautifulSoup(src, "lxml")

# Links zu den Märchen
urls= []
# Titel der einzelnen Märchen
titel = []
#Maerchentext
minhalt = []
    
for list in soup.find_all("ul", class_="bluelink"):
    for link in list.find_all("li"):
        a = link.find("a")
        urls.append(a.attrs["href"])
        titel.append(a.get_text())
        

for x in urls:
    r = requests.get(x)
    r.encoding = "utf-8"
    quelle = r.content
    soupi = BeautifulSoup(quelle, "lxml")
    for txt in soupi.find_all("div", class_="text"):
        minhalt.append(txt.get_text())


In [2]:
# Dictionary
maerchen = dict(zip(titel, minhalt))

NameError: name 'titel' is not defined

In [3]:
# JSON für das DataFrame
with open("\map\maerchen.json", "w") as file:
     json.dump(maerchen, file)

NameError: name 'maerchen' is not defined

In [2]:
# Maerchen laden
with open('maerchen.json', 'r') as f:
    data = json.load(f)

In [3]:
print(data)

{'Der Froschkönig oder der eiserne Heinrich': 'In den alten Zeiten, wo das Wünschen noch geholfen hat, lebte ein König, dessen Töchter waren alle schön; aber die jüngste war so schön, daß die Sonne selber, die doch so vieles gesehen hat, sich verwunderte, sooft sie ihr ins Gesicht schien. Nahe bei dem Schlosse des Königs lag ein großer dunkler Wald, und in dem Walde unter einer alten Linde war ein Brunnen; wenn nun der Tag recht heiß war, so ging das Königskind hinaus in den Wald und setzte sich an den Rand des kühlen Brunnens - und wenn sie Langeweile hatte, so nahm sie eine goldene Kugel, warf sie in die Höhe und fing sie wieder; und das war ihr liebstes Spielwerk.\n\nNun trug es sich einmal zu, daß die goldene Kugel der Königstochter nicht in ihr Händchen fiel, das sie in die Höhe gehalten hatte, sondern vorbei auf die Erde schlug und geradezu ins Wasser hineinrollte. Die Königstochter folgte ihr mit den Augen nach, aber die Kugel verschwand, und der Brunnen war tief, so tief, daß m

In [3]:
df = pd.DataFrame(list(data.items()),columns = ['Titel','Text']) 


In [4]:
# lower case
df["Text"] = df["Text"].str.lower()


In [5]:
#Stopwords entfernen
stopset = stopwords.words('german')
df["Text"] = df["Text"].apply(lambda x: " ".join([item for item in x.split() if item not in stopset]))


In [6]:
# Satzzeichen entfernen
df["Text"].replace(to_replace=r'[^\w\s]', value='', inplace=True, regex=True)
# newline entfernen
df["Text"].replace(to_replace=r'/\r?\n|\r/', value='', inplace=True, regex=True)

# Spalte für die Vektoren später erstellen
df["Doc2Vec"] = df["Text"]
colvector = df["Doc2Vec"]
df["TFIDF"] = df["Text"]
df["WikiVec"] = df["Text"]


In [7]:
df_hljla = df[["Titel", "Text"]].copy()


In [8]:
# Tokenisieren für das Modell Doc2Vec
df["Text"] = df["Text"].apply(word_tokenize)




Titel  \
0        Der Froschkönig oder der eiserne Heinrich   
1                   Katze und Maus in Gesellschaft   
2                                       Marienkind   
3    Von einem, der auszog, das Fürchten zu lernen   
4          Der Wolf und die sieben jungen Geißlein   
..                                             ...   
218                                      Hans Dumm   
219                                       Blaubart   
220                                 Hurleburlebutz   
221                                     Der Okerlo   
222                           Prinzessin Mäusehaut   

                                                  Text  \
0    [alten, zeiten, wünschen, geholfen, hat, lebte...   
1    [katze, bekanntschaft, maus, gemacht, soviel, ...   
2    [großen, walde, lebte, holzhacker, frau, einzi...   
3    [vater, zwei, söhne, davon, älteste, klug, ges...   
4    [alte, geiß, sieben, junge, geißlein, lieb, mu...   
..                                                 ...   
218  [könig, lebte, tochter, einziges, kind, war, v...   
219  [walde, lebte, mann, drei, söhne, schöne, toch...   
220  [könig, verirrte, jagd, trat, kleines, weißes,...   
221  [königin, setzte, kind, goldenen, wiege, aufs,...   
222  [könig, drei, töchter, wissen, liebsten, hätte...   

                                               Doc2Vec  \
0    alten zeiten wünschen geholfen hat lebte könig...   
1    katze bekanntschaft maus gemacht soviel großer...   
2    großen walde lebte holzhacker frau einziges ki...   
3    vater zwei söhne davon älteste klug gescheit w...   
4    alte geiß sieben junge geißlein lieb mutter ki...   
..                                                 ...   
218  könig lebte tochter einziges kind war vergnügt...   
219  walde lebte mann drei söhne schöne tochter kam...   
220  könig verirrte jagd trat kleines weißes männch...   
221  königin setzte kind goldenen wiege aufs meer l...   
222  könig drei töchter wissen liebsten hätte ließ ...   

                                                 TFIDF  \
0    alten zeiten wünschen geholfen hat lebte könig...   
1    katze bekanntschaft maus gemacht soviel großer...   
2    großen walde lebte holzhacker frau einziges ki...   
3    vater zwei söhne davon älteste klug gescheit w...   
4    alte geiß sieben junge geißlein lieb mutter ki...   
..                                                 ...   
218  könig lebte tochter einziges kind war vergnügt...   
219  walde lebte mann drei söhne schöne tochter kam...   
220  könig verirrte jagd trat kleines weißes männch...   
221  königin setzte kind goldenen wiege aufs meer l...   
222  könig drei töchter wissen liebsten hätte ließ ...   

                                               WikiVec  
0    alten zeiten wünschen geholfen hat lebte könig...  
1    katze bekanntschaft maus gemacht soviel großer...  
2    großen walde lebte holzhacker frau einziges ki...  
3    vater zwei söhne davon älteste klug gescheit w...  
4    alte geiß sieben junge geißlein lieb mutter ki...  
..                                                 ...  
218  könig lebte tochter einziges kind war vergnügt...  
219  walde lebte mann drei söhne schöne tochter kam...  
220  könig verirrte jagd trat kleines weißes männch...  
221  königin setzte kind goldenen wiege aufs meer l...  
222  könig drei töchter wissen liebsten hätte ließ ...  

[223 rows x 5 columns]

In [101]:
df

Titel  \
0        Der Froschkönig oder der eiserne Heinrich   
1                   Katze und Maus in Gesellschaft   
2                                       Marienkind   
3    Von einem, der auszog, das Fürchten zu lernen   
4          Der Wolf und die sieben jungen Geißlein   
..                                             ...   
218                                      Hans Dumm   
219                                       Blaubart   
220                                 Hurleburlebutz   
221                                     Der Okerlo   
222                           Prinzessin Mäusehaut   

                                                  Text  \
0    [alten, zeiten, wünschen, geholfen, hat, lebte...   
1    [katze, bekanntschaft, maus, gemacht, soviel, ...   
2    [großen, walde, lebte, holzhacker, frau, einzi...   
3    [vater, zwei, söhne, davon, älteste, klug, ges...   
4    [alte, geiß, sieben, junge, geißlein, lieb, mu...   
..                                                 ...   
218  [könig, lebte, tochter, einziges, kind, war, v...   
219  [walde, lebte, mann, drei, söhne, schöne, toch...   
220  [könig, verirrte, jagd, trat, kleines, weißes,...   
221  [königin, setzte, kind, goldenen, wiege, aufs,...   
222  [könig, drei, töchter, wissen, liebsten, hätte...   

                                               Doc2Vec  \
0    [alten, zeiten, wünschen, geholfen, hat, lebte...   
1    [katze, bekanntschaft, maus, gemacht, soviel, ...   
2    [großen, walde, lebte, holzhacker, frau, einzi...   
3    [vater, zwei, söhne, davon, älteste, klug, ges...   
4    [alte, geiß, sieben, junge, geißlein, lieb, mu...   
..                                                 ...   
218  [könig, lebte, tochter, einziges, kind, war, v...   
219  [walde, lebte, mann, drei, söhne, schöne, toch...   
220  [könig, verirrte, jagd, trat, kleines, weißes,...   
221  [königin, setzte, kind, goldenen, wiege, aufs,...   
222  [könig, drei, töchter, wissen, liebsten, hätte...   

                                                 TFIDF  \
0    [alten, zeiten, wünschen, geholfen, hat, lebte...   
1    [katze, bekanntschaft, maus, gemacht, soviel, ...   
2    [großen, walde, lebte, holzhacker, frau, einzi...   
3    [vater, zwei, söhne, davon, älteste, klug, ges...   
4    [alte, geiß, sieben, junge, geißlein, lieb, mu...   
..                                                 ...   
218  [könig, lebte, tochter, einziges, kind, war, v...   
219  [walde, lebte, mann, drei, söhne, schöne, toch...   
220  [könig, verirrte, jagd, trat, kleines, weißes,...   
221  [königin, setzte, kind, goldenen, wiege, aufs,...   
222  [könig, drei, töchter, wissen, liebsten, hätte...   

                                               WikiVec    Erscheinungsjahr  
0    [alten, zeiten, wünschen, geholfen, hat, lebte...                1812  
1    [katze, bekanntschaft, maus, gemacht, soviel, ...                1812  
2    [großen, walde, lebte, holzhacker, frau, einzi...                1812  
3    [vater, zwei, söhne, davon, älteste, klug, ges...                1812  
4    [alte, geiß, sieben, junge, geißlein, lieb, mu...                1812  
..                                                 ...                 ...  
218  [könig, lebte, tochter, einziges, kind, war, v...            nur 1812  
219  [walde, lebte, mann, drei, söhne, schöne, toch...  übersetzt nur 1812  
220  [könig, verirrte, jagd, trat, kleines, weißes,...            nur 1812  
221  [königin, setzte, kind, goldenen, wiege, aufs,...  übersetzt nur 1812  
222  [könig, drei, töchter, wissen, liebsten, hätte...            nur 1812  

[223 rows x 6 columns]

In [7]:
# in eine Variable packen
maerchen = df["Text"]

In [22]:
#Erscheinungsjahre der Märchen in das Dataframe hinzufügen
ejahr = pd.read_csv("erscheinungsjahr.csv", sep=";") 
ejahr = ejahr["Jahr"]


In [23]:
df["Erscheinungsjahr"] = ejahr
erscheinung = df["Erscheinungsjahr"]
#df

# TF IDF

In [41]:
df["TFIDF"] = df["TFIDF"].apply(word_tokenize)

TypeError: expected string or bytes-like object

In [53]:
from sklearn.feature_extraction.text import TfidfVectorizer
#Vektorisieren mittels TF-IDF
modified_tfidf = [' '.join(i) for i in df["TFIDF"]]
tf_idf = TfidfVectorizer().fit_transform(modified_tfidf)
tf_idf

<223x14619 sparse matrix of type '<class 'numpy.float64'>'
	with 78150 stored elements in Compressed Sparse Row format>

## Kosinus Ähnlichkeit berechnen

In [85]:

from sklearn.metrics.pairwise import cosine_similarity  
cosine_similarities = cosine_similarity(tf_idf, tf_idf)
cosine_similarities

array([[1.        , 0.04146213, 0.08640595, ..., 0.08242097, 0.05179806,
        0.08814927],
       [0.04146213, 1.        , 0.04789814, ..., 0.04826395, 0.04197008,
        0.03190012],
       [0.08640595, 0.04789814, 1.        , ..., 0.07378941, 0.11143587,
        0.06660996],
       ...,
       [0.08242097, 0.04826395, 0.07378941, ..., 1.        , 0.08103245,
        0.12348445],
       [0.05179806, 0.04197008, 0.11143587, ..., 0.08103245, 1.        ,
        0.04335352],
       [0.08814927, 0.03190012, 0.06660996, ..., 0.12348445, 0.04335352,
        1.        ]])

In [90]:

dftf = pd.DataFrame(columns=["Märchen", "am ähnlichsten", "cos(\u03B8)"])

for i in range(len(modified_tfidf)):
    cosine_similarities = cosine_similarity(tf_idf[i:i+1], tf_idf).flatten()
    cosine_similarities = list(enumerate(cosine_similarities))
    cosine_similarities.pop(i)
    most_similar, similarity = max(cosine_similarities, key=lambda t:t[1])
    dftf.loc[len(dftf)] = [modified_tfidf[i], modified_tfidf[most_similar], similarity]
#Die Titel in die Spalte "Märchen" einfügen, damit da nicht der Text steht.  
dftf["Märchen"]=df["Titel"]
#dftf.to_csv("tfidf_cosine.csv")
dftf

Märchen  \
0        Der Froschkönig oder der eiserne Heinrich   
1                   Katze und Maus in Gesellschaft   
2                                       Marienkind   
3    Von einem, der auszog, das Fürchten zu lernen   
4          Der Wolf und die sieben jungen Geißlein   
..                                             ...   
218                                      Hans Dumm   
219                                       Blaubart   
220                                 Hurleburlebutz   
221                                     Der Okerlo   
222                           Prinzessin Mäusehaut   

                                        am ähnlichsten         θ  
0    könig großen wald schloß darin lief wild art h...  0.172659  
1    trug zu katze walde herrn fuchs begegnete dach...  0.252642  
2    müller armut geraten mehr mühle großen apfelba...  0.213880  
3    zwei brüder reicher armer reiche goldschmied b...  0.283662  
4    wolf fuchs sich wolf wollte mußte fuchs tun sc...  0.336449  
..                                                 ...       ...  
218  mann frau einziges kind lebten abseits gelegen...  0.308167  
219  könig königin lebten frieden miteinander zwölf...  0.224119  
220  zeiten könig schönen lustgarten schloß darin s...  0.292621  
221  frau rechte hexe zwei töchter hässlich böse li...  0.181903  
222  armer bauer land kleines häuschen alleinige to...  0.173084  

[223 rows x 3 columns]

Problem: 
In dem DataFrame werden die Texte der Märchen angezeigt und nicht die Titel. Das ist nicht so übersichtlich. Deswegen wird im Folgenden mithilfe eines Dictionarys die Spalte "am ähnlichsten" zu den Texten der richtige Titel zugeordnet. Dies wird gemacht, indem die Spalte "am ähnlichsten" in eine Liste gepackt wird, darüber iteriert wird und mit den Keys des erstellten Dictionarys verglichen wird. Der jeweiligen Text des Märchens wird mit dem Titel in der Liste "liste" ersetzt und anschließend wieder in das DataFrame gepackt.

In [91]:
df_tempp = dftf.copy()

In [92]:
#Liste des Textes der ähnlichsten Märchen
liste=df_tempp["am ähnlichsten"].tolist()


In [93]:
# Texte der Märchen extrahoieren, damit die als Dictionary Key verwendet werden können
dictliste= df_hljla["Text"].tolist()


In [94]:
#kann auf 20 Characters reduziert werden. Beschleunigt den Prozess und ist übersichtlicher
for x in range(len(dictliste)):
    dictliste[x] = dictliste[x][:20]
dictliste

['alten zeiten wünsche',
 'katze bekanntschaft ',
 'großen walde lebte h',
 'vater zwei söhne dav',
 'alte geiß sieben jun',
 'alter könig krank da',
 'bauer kuh markt getr',
 'wunderlicher spielma',
 'könig königin lebten',
 'hähnchen sprach hühn',
 'brüderchen nahm schw',
 'mann frau wünschten ',
 'mann starb frau frau',
 'mädchen faul spinnen',
 'großen walde wohnte ',
 'armer mann konnte ei',
 'schon lange her lebt',
 'dorfe wohnte arme al',
 'fischer frau wohnten',
 'sommermorgen sass sc',
 'reichen manne wurde ',
 'königssohn bekam lus',
 'mäuschen vögelchen b',
 'witwe zwei töchter d',
 'mann sieben söhne im',
 'kleines süßes mädche',
 'mann esel schon lang',
 'lande große klage wi',
 'arme frau gebar söhn',
 'läuschen flöhchen le',
 'müller armut geraten',
 'hansens mutter fragt',
 'schweiz lebte alter ',
 'mann tochter hieß kl',
 'trug zu liebe gott s',
 'zeiten schneider dre',
 'armer bauersmann saß',
 'erstes märchen alter',
 'erstes märchen schus',
 'müller schöne tochte',


In [95]:
df_hljla["Text"] = dictliste

In [96]:
#Dictionary erstellen, das Titel und Text der Märchen enthält
simski= dict(zip(df_hljla["Text"], df_hljla["Titel"]))
simski

{'alten zeiten wünsche': 'Der Froschkönig oder der eiserne Heinrich',
 'katze bekanntschaft ': 'Katze und Maus in Gesellschaft',
 'großen walde lebte h': 'Marienkind',
 'vater zwei söhne dav': 'Von einem, der auszog, das Fürchten zu lernen',
 'alte geiß sieben jun': 'Der Wolf und die sieben jungen Geißlein',
 'alter könig krank da': 'Der treue Johannes',
 'bauer kuh markt getr': 'Der gute Handel',
 'wunderlicher spielma': 'Der wunderliche Spielmann',
 'könig königin lebten': 'Die zwölf Brüder',
 'hähnchen sprach hühn': 'Das Lumpengesindel',
 'brüderchen nahm schw': 'Brüderchen und Schwesterchen',
 'mann frau wünschten ': 'Rapunzel',
 'mann starb frau frau': 'Die drei Männlein im Walde',
 'mädchen faul spinnen': 'Die drei Spinnerinnen',
 'großen walde wohnte ': 'Hänsel und Gretel',
 'armer mann konnte ei': 'Die drei Schlangenblätter',
 'schon lange her lebt': 'Die weiße Schlange',
 'dorfe wohnte arme al': 'Strohhalm, Kohle und Bohne',
 'fischer frau wohnten': 'Von dem Fischer und seiner

In [97]:
#kann auf 20 Characters reduziert werden. Beschleunigt den Prozess und ist übersichtlicher
for x in range(len(liste)):
    liste[x] = liste[x][:20]


In [98]:
#Die zugehörigen Titel der Märchen mithilfe eines Dictionary rausfinden, damit in der Zelle nicht der Text, sondern Titel steht
for s in range (len(liste)):
    simon = liste[s]
    simon = simski.get(simon)
    liste[s] = simon
liste

['Der Eisenhans',
 'Der Fuchs und die Katze',
 'Das Mädchen ohne Hände',
 'Die zwei Brüder',
 'Der Wolf und der Fuchs',
 'Die drei Schlangenblätter',
 'Die klugen Leute',
 'König Drosselbart',
 'Die sechs Schwäne',
 'Von dem Tode des Hühnchens',
 'Die sechs Schwäne',
 'Die sechs Diener',
 'Die sechs Schwäne',
 'Die Schlickerlinge',
 'Das kluge Gretel',
 'Die zwei Brüder',
 'Der Königssohn, der sich vor nichts fürchtet',
 'Der Okerlo',
 'Die Goldkinder',
 'Vom klugen Schneiderlein',
 'Die beiden Königskinder',
 'Die sechs Diener',
 'Katze und Maus in Gesellschaft',
 'Die drei Männlein im Walde',
 'Die zwölf Brüder',
 'Der Wolf und der Fuchs',
 'Die drei Glückskinder',
 'Die zertanzten Schuhe',
 'Das Mädchen ohne Hände',
 'Die drei Männlein im Walde',
 'Die Nelke',
 'Der starke Hans',
 'Der König vom goldenen Berg',
 'Der starke Hans',
 'Die beiden Wanderer',
 'Die beiden Wanderer',
 'Von einem, der auszog, das Fürchten zu lernen',
 'Der Fuchs und die Katze',
 'Die beiden Wanderer',
 'Di

In [99]:
dftf["am ähnlichsten"]=liste 

Daraus ergibt sich dann das folgende DataFrame, das die Titel der Märchen und die Kosinus Ähnlichkeit enthält.

In [100]:
dftf["Märchen"]=df["Titel"]
#dftf.to_csv("tfidf_kosinus.csv")
dftf

Märchen           am ähnlichsten  \
0        Der Froschkönig oder der eiserne Heinrich            Der Eisenhans   
1                   Katze und Maus in Gesellschaft  Der Fuchs und die Katze   
2                                       Marienkind   Das Mädchen ohne Hände   
3    Von einem, der auszog, das Fürchten zu lernen          Die zwei Brüder   
4          Der Wolf und die sieben jungen Geißlein   Der Wolf und der Fuchs   
..                                             ...                      ...   
218                                      Hans Dumm          Der starke Hans   
219                                       Blaubart         Die zwölf Brüder   
220                                 Hurleburlebutz        Der goldene Vogel   
221                                     Der Okerlo       Der liebste Roland   
222                           Prinzessin Mäusehaut  Die kluge Bauerntochter   

            θ  
0    0.172659  
1    0.252642  
2    0.213880  
3    0.283662  
4    0.336449  
..        ...  
218  0.308167  
219  0.224119  
220  0.292621  
221  0.181903  
222  0.173084  

[223 rows x 3 columns]

In [20]:

similarities_sparse = cosine_similarity(tf_idf,dense_output=False)
print('pairwise sparse output:\n {}\n'.format(similarities_sparse))

pairwise sparse output:
   (0, 139)	0.0060004746545242104
  (0, 65)	0.028548962691520925
  (0, 170)	0.03140746751102044
  (0, 156)	0.021811535623633017
  (0, 215)	0.01866892272887877
  (0, 203)	0.006037061766628277
  (0, 102)	0.021772731395854835
  (0, 210)	0.03288321878989892
  (0, 190)	0.02027082228089638
  (0, 189)	0.026445698148173925
  (0, 207)	0.024509313049676476
  (0, 108)	0.06377204704233515
  (0, 149)	0.03890558892451025
  (0, 142)	0.03793968327267532
  (0, 77)	0.044944603748754974
  (0, 173)	0.013251088509659423
  (0, 167)	0.022081597376062814
  (0, 74)	0.04002746473044481
  (0, 41)	0.04705316435851947
  (0, 40)	0.047527692872451184
  (0, 212)	0.017049418648307984
  (0, 159)	0.07995997953052275
  (0, 150)	0.06800919513007289
  (0, 194)	0.02055245227543514
  (0, 184)	0.022320589726386453
  :	:
  (222, 63)	0.069742433812707
  (222, 56)	0.09936880060535552
  (222, 191)	0.07850584628668354
  (222, 64)	0.1716833409231588
  (222, 87)	0.09816300536732206
  (222, 201)	0.039092570429

# Doc2Vec

In [81]:
#Die Dokumente brauchen für Doc2Vec jeweils einen einzigartigen Identifier
documents = [TaggedDocument(doc, [i]) for i, doc in enumerate(maerchen)]
#documents

## PV-DBOW

In [12]:
# PV-DBOW Modell für Doc2Vec trainieren
cores = multiprocessing.cpu_count()

model_dbow = Doc2Vec(vector_size=50, min_count=2, window=5, workers=cores, dm=0, epochs=20)
#IBM Paper Hyperparameters
#model = Doc2Vec(vector_size=300, window=15, min_count=5, negative=5, workers=cores, sample=1e-5, epochs=20)
model_dbow.build_vocab(documents)
model_dbow.train(documents, epochs=model_dbow.iter, total_examples=model_dbow.corpus_count)
model_dbow.save("pv_dbow.model")


<ipython-input-12-20707d5ca1af>:8: DeprecationWarning: Call to deprecated `iter` (Attribute will be removed in 4.0.0, use self.epochs instead).
  model_dbow.train(documents, epochs=model_dbow.iter, total_examples=model_dbow.corpus_count)


In [8]:
model_dbow = Doc2Vec.load("pv_dbow.model")

In [9]:
# Vektoren der einzelnen Maerchen erzeugen
#docvectors = [model_dbow.infer_vector((word_tokenize(df["Doc2Vec"][i]))) 
 #           for i in range(0,len(df["Doc2Vec"]))]

docvectors = [model_dbow.infer_vector((word_tokenize(df["Doc2Vec"][i]))) 
            for i in range(0,len(df["Doc2Vec"]))]


In [11]:
df_titel = df["Titel"].copy()

In [12]:
#Welche Märchen sind denen aus dem Modell am ähnlichsten?
titel = []
most_sim = []
#model_dbow.wv.vocab
for doc in range(len(docvectors)):
    print("Dokument", df_titel.iloc[doc], model_dbow.docvecs.most_similar(positive=[docvectors[doc]], topn=2)[1])
    titel.append(df_titel.iloc[doc])
    most_sim.append(model_dbow.docvecs.most_similar(positive=[docvectors[doc]])[1])
    

Dokument Der Froschkönig oder der eiserne Heinrich (155, 0.5098206996917725)
Dokument Katze und Maus in Gesellschaft (168, 0.6305437684059143)
Dokument Marienkind (202, 0.6041646599769592)
Dokument Von einem, der auszog, das Fürchten zu lernen (150, 0.5582839250564575)
Dokument Der Wolf und die sieben jungen Geißlein (205, 0.5968629717826843)
Dokument Der treue Johannes (15, 0.5122947096824646)
Dokument Der gute Handel (97, 0.5789322853088379)
Dokument Der wunderliche Spielmann (71, 0.6105112433433533)
Dokument Die zwölf Brüder (48, 0.7460495233535767)
Dokument Das Lumpengesindel (40, 0.6984402537345886)
Dokument Brüderchen und Schwesterchen (108, 0.587174117565155)
Dokument Rapunzel (77, 0.5356643199920654)
Dokument Die drei Männlein im Walde (134, 0.5785261392593384)
Dokument Die drei Spinnerinnen (156, 0.6761243939399719)
Dokument Hänsel und Gretel (76, 0.5620051622390747)
Dokument Die drei Schlangenblätter (43, 0.5578227639198303)
Dokument Die weiße Schlange (174, 0.558406054973602

In [13]:
#Welche Märchen sind den aus dem Modell am unähnllichsten?
most_dis=[]
for doc in range(len(docvectors)):
    print("Dokument", df_titel.iloc[doc], model_dbow.docvecs.most_similar(negative=[docvectors[doc]], topn=2)[0])
    most_dis.append(model_dbow.docvecs.most_similar(negative=[docvectors[doc]])[0])

Dokument Der Froschkönig oder der eiserne Heinrich (185, 0.025408267974853516)
Dokument Katze und Maus in Gesellschaft (75, 0.08328421413898468)
Dokument Marienkind (118, 0.004274505190551281)
Dokument Von einem, der auszog, das Fürchten zu lernen (203, -0.020198337733745575)
Dokument Der Wolf und die sieben jungen Geißlein (165, 0.007722623646259308)
Dokument Der treue Johannes (63, 0.0698062926530838)
Dokument Der gute Handel (68, 0.02295629307627678)
Dokument Der wunderliche Spielmann (119, 0.006423947401344776)
Dokument Die zwölf Brüder (109, 0.03138710558414459)
Dokument Das Lumpengesindel (135, 0.009550869464874268)
Dokument Brüderchen und Schwesterchen (91, -0.058842867612838745)
Dokument Rapunzel (81, 0.023734796792268753)
Dokument Die drei Männlein im Walde (174, 0.06296076625585556)
Dokument Die drei Spinnerinnen (14, -0.004785254597663879)
Dokument Hänsel und Gretel (32, -0.015918321907520294)
Dokument Die drei Schlangenblätter (1, 0.04762277752161026)
Dokument Die weiße Sch

In [15]:
df_temp = pd.DataFrame(columns=["Märchen", "ähnlichstes Märchen"])
df_temp["Märchen"] = titel
df_temp["ähnlichstes Märchen"] = most_sim
df_temp["unähnlichstes Märchen"] = most_dis
df_temp.to_csv("modelld2v_ähnlichemärchen.csv")
df_temp

Märchen        ähnlichstes Märchen  \
0        Der Froschkönig oder der eiserne Heinrich  (155, 0.5098206996917725)   
1                   Katze und Maus in Gesellschaft  (168, 0.6305437684059143)   
2                                       Marienkind  (202, 0.6041646599769592)   
3    Von einem, der auszog, das Fürchten zu lernen  (150, 0.5582839250564575)   
4          Der Wolf und die sieben jungen Geißlein  (205, 0.5968629717826843)   
..                                             ...                        ...   
218                                      Hans Dumm  (152, 0.6548411250114441)   
219                                       Blaubart   (13, 0.5264087915420532)   
220                                 Hurleburlebutz   (65, 0.6182067394256592)   
221                                     Der Okerlo  (156, 0.6822659969329834)   
222                           Prinzessin Mäusehaut   (66, 0.6736119985580444)   

            unähnlichstes Märchen  
0     (185, 0.025408267974853516)  
1       (75, 0.08328421413898468)  
2     (118, 0.004274505190551281)  
3    (203, -0.020198337733745575)  
4     (165, 0.007722623646259308)  
..                            ...  
218   (4, -0.0013439767062664032)  
219     (14, 0.05074000358581543)  
220    (19, 0.004000222776085138)  
221     (82, 0.09062906354665756)  
222    (25, 0.023405497893691063)  

[223 rows x 3 columns]

In [13]:
#Liste bestehend aus Liste erstellen, damit das in das Dataframe gepackt werden kann.
dcv = np.array(docvectors).tolist()
# zu Spalte in Dataframe hinzufügen
df["Doc2Vec"] = dcv


In [14]:
#Dataframe tokenisieren
df["Doc2Vec"]=df["Doc2Vec"].apply(word_tokenize)
modified_d2v = [' '.join(i) for i in df["Doc2Vec"]]

## Kosinus Ähnlichkeit berechnen


In [66]:
# Messen der Kosinus Ähnlichkeit und ausgeben, welches das ähnlichste Märchen ist
from sklearn.metrics.pairwise import cosine_similarity 
dfd2v = pd.DataFrame(columns=["Märchen", "am ähnlichsten", "cos(\u03B8)"])

for i in range(len(modified_d2v)):
    cosine_similarities = cosine_similarity(docvectors[i:i+1], docvectors).flatten()
    cosine_similarities = list(enumerate(cosine_similarities))
    cosine_similarities.pop(i)
    most_similar, similarity = max(cosine_similarities, key=lambda t:t[1])
    dfd2v.loc[len(dfd2v)] = [modified_d2v[i], modified_d2v[most_similar], similarity]
    
dfd2v["Märchen"] = df["Titel"]

In [67]:

df_temp1 = dfd2v.copy()
listed2v=df_temp1["am ähnlichsten"].tolist()


In [68]:
#kann auf 20 Characters reduziert werden. Beschleunigt den Prozess und ist übersichtlicher
for x in range(len(listed2v)):
    listed2v[x] = listed2v[x][:20]
listed2v

['junger hirt gern hei',
 'armes frommes mädche',
 'dreihundert jahre he',
 'könig drei söhne gle',
 'wolf fuchs sich wolf',
 'zauberin drei söhne ',
 'tages holte bauer ha',
 'fuchs erzählte wolf ',
 'jagte könig großen w',
 'hühnchen hähnchen wo',
 'mutter büblein siebe',
 'steinalter mann auge',
 'junger hirt gern hei',
 'mädchen schön faul n',
 'köchin hieß gretel t',
 'armer mann zwölf kin',
 'königstochter schloß',
 'mäuschen vögelchen b',
 'drei frauen blumen v',
 'schneider großer pra',
 'kind eigensinnig tat',
 'drei handwerksbursch',
 'brüderchen schwester',
 'fuhr armes dienstmäd',
 'kind eigensinnig tat',
 'alte geiß sieben jun',
 'gott herr tiere ersc',
 'armer mann vier söhn',
 'kleines mädchen eige',
 'fuchs kam wiese herd',
 'mutter büblein siebe',
 'glücklich herr wohl ',
 'königssohn braut lie',
 'mann hieß frieder fr',
 'armes frommes bäuerl',
 'drei feldscherer rei',
 'armer bauer namens k',
 'fuchs kam wiese herd',
 'kleines mädchen drei',
 'brüderchen schwester',


In [69]:
#Die zugehörigen Titel der Märchen mithilfe eines Dictionary rausfinden, damit in der Zelle nicht der Text, sondern Titel steht
for s in range (len(listed2v)):
    simon = listed2v[s]
    simon = simski.get(simon)
    listed2v[s] = simon
listed2v

['Die Brautschau',
 'Der süße Brei',
 'Die zwölf Apostel',
 'Die drei Faulen',
 'Der Wolf und der Fuchs',
 'Die Kristallkugel',
 'Die klugen Leute',
 'Der Wolf und der Mensch',
 'Die sechs Schwäne',
 'Herr Korbes',
 'Das Totenhemdchen',
 'Der alte Großvater und der Enkel',
 'Die Brautschau',
 'Die Schlickerlinge',
 'Das kluge Gretel',
 'Der Gevatter Tod',
 'Das Meerhäschen',
 'Von dem Mäuschen, Vögelchen und der Bratwurst',
 'Rätselmärchen',
 'Der Riese und der Schneider',
 'Das eigensinnige Kind',
 'Die drei Handwerksburschen',
 'Das Lämmchen und Fischchen',
 'Die Alte im Wald',
 'Das eigensinnige Kind',
 'Der Wolf und die sieben jungen Geißlein',
 'Des Herrn und des Teufels Getier',
 'Die vier kunstreichen Brüder',
 'Frau Trude',
 'Der Fuchs und die Gänse',
 'Das Totenhemdchen',
 'Der kluge Knecht',
 'Die zwölf Jäger',
 'Der Frieder und das Katherlieschen',
 'Das Bürle im Himmel',
 'Die drei Feldscherer',
 'Doktor Allwissend',
 'Der Fuchs und die Gänse',
 'Die Hand mit dem Messer',
 

In [70]:
dfd2v["am ähnlichsten"]=listed2v
dfd2v["Märchen"]=df["Titel"]
dfd2v.to_csv("doc2vec_kosinus.csv")
dfd2v

Märchen          am ähnlichsten  \
0        Der Froschkönig oder der eiserne Heinrich          Die Brautschau   
1                   Katze und Maus in Gesellschaft           Der süße Brei   
2                                       Marienkind       Die zwölf Apostel   
3    Von einem, der auszog, das Fürchten zu lernen         Die drei Faulen   
4          Der Wolf und die sieben jungen Geißlein  Der Wolf und der Fuchs   
..                                             ...                     ...   
218                                      Hans Dumm           Hans heiratet   
219                                       Blaubart   Die drei Spinnerinnen   
220                                 Hurleburlebutz           Häsichenbraut   
221                                     Der Okerlo           Rätselmärchen   
222                           Prinzessin Mäusehaut         Die zwölf Jäger   

     similarity%  
0       0.482148  
1       0.607841  
2       0.582808  
3       0.493589  
4       0.568027  
..           ...  
218     0.596794  
219     0.535121  
220     0.623302  
221     0.682499  
222     0.611064  

[223 rows x 3 columns]

In [38]:
df.to_csv("vollstaendigesDataframe.csv")

### Wikipedia Doc2Vec

In [1]:
# nach Tutorial von Gensimm Developern: https://markroxor.github.io/gensim/static/notebooks/doc2vec-wikipedia.html
from gensim.corpora.wikicorpus import WikiCorpus
from gensim.models.doc2vec import Doc2Vec, TaggedDocument
from pprint import pprint
import multiprocessing
#gensim wikicorpus
wiki = WikiCorpus("dewiki-latest-pages-articles.xml.bz2")


/Users/nicolaswerner/.pyenv/versions/miniconda3-4.7.12/envs/mapenv/lib/python3.8/site-packages/gensim/utils.py:1268: UserWarning: detected OSX with python3.8+; aliasing chunkize to chunkize_serial
  warnings.warn("detected %s; aliasing chunkize to chunkize_serial" % entity)


In [ ]:
class TaggedWikiDocument(object):
    def __init__(self, wiki):
        self.wiki = wiki
        self.wiki.metadata = True
    def __iter__(self):
        for content, (page_id, title) in self.wiki.get_texts():
            yield TaggedDocument([c.decode("utf-8") for c in content], [title])
            

In [ ]:

    wiki = WikiCorpus(r'C:\Users\Studierende\PycharmProjects\NicolasWerner\dewiki-latest-pages-articles.xml.bz2')

#c.encode().decode ist keine elegante Lösung, aber die, die bei mir funktioniert :(
    class TaggedWikiDocument(object):
        def __init__(self, wiki):
            self.wiki = wiki
            self.wiki.metadata = True
        def __iter__(self):
            for content, (page_id, title) in self.wiki.get_texts():
                yield TaggedDocument([c.encode().decode("utf-8") for c in content], [title])


    documentsw = TaggedWikiDocument(wiki)



    cores = multiprocessing.cpu_count()

    model_dbow_w = Doc2Vec(vector_size=300, min_count=5, negative=5, window=15, workers=cores, dm=0, epochs=20, alpha=0.025, min_alpha=0.0001, sample=1e-5)
    model_dbow_w.build_vocab(documentsw)
    model_dbow_w.train(documentsw, epochs=model_dbow_w.iter, total_examples=model_dbow_w.corpus_count)
    model_dbow_w.save("wiki_dbow.model")
   # models[1].save("wiki_dm.model")


In [16]:
model_wiki_dbow = Doc2Vec.load("wiki_dbow.model")

In [17]:
wikivectors = [model_wiki_dbow.infer_vector((word_tokenize(df["WikiVec"][i]))) 
            for i in range(0,len(df["WikiVec"]))]

In [18]:
#ähnlichste Wikipedia Einträge
titelw = []
most_simw= []
#model_dbow.wv.vocab
for doc in range(len(wikivectors)):
    print("Dokument", df_titel.iloc[doc], model_wiki_dbow.docvecs.most_similar(positive=[wikivectors[doc]], topn=2))
    titelw.append(df_titel.iloc[doc])
    most_simw.append(model_wiki_dbow.docvecs.most_similar(positive=[wikivectors[doc]])[1])

Dokument Der Froschkönig oder der eiserne Heinrich [('Schneewittchen (1959)', 0.6155596971511841), ('Kuperan', 0.6097391843795776)]
Dokument Katze und Maus in Gesellschaft [('Nebelmännle', 0.5368053317070007), ('Bärenhunger', 0.5354288816452026)]
Dokument Marienkind [('Schneewittchen (1959)', 0.5963383913040161), ('Editha und die Hirschkuh', 0.5799908638000488)]
Dokument Von einem, der auszog, das Fürchten zu lernen [('Kuperan', 0.611905574798584), ('Sagenweg Sagenhaftes Wölzertal', 0.6022475957870483)]
Dokument Der Wolf und die sieben jungen Geißlein [('Der gastliche Kalbskopf', 0.5909982919692993), ('Die faule Spinnerin', 0.5900070071220398)]
Dokument Der treue Johannes [('Schneewittchen (1959)', 0.6037840247154236), ('Die hagere Liese', 0.5858985185623169)]
Dokument Der gute Handel [('Der gute Handel', 0.6393460035324097), ('Von dem Schneider, der bald reich wurde', 0.5678902864456177)]
Dokument Der wunderliche Spielmann [('Kuperan', 0.5813015699386597), ('Sagenweg Sagenhaftes Wölze

Dokument Der Gaudieb und sein Meister [('Von dem Schneider, der bald reich wurde', 0.5944288969039917), ('Die faule Spinnerin', 0.5676412582397461)]
Dokument Jorinde und Joringel [('Kuperan', 0.5848924517631531), ('Galinthias', 0.572579026222229)]
Dokument Die drei Glückskinder [('Sagenweg Sagenhaftes Wölzertal', 0.541602611541748), ('Wuotis-Heer', 0.5236983299255371)]
Dokument Sechse kommen durch die ganze Welt [('Der Ranzen, das Hütlein und das Hörnlein', 0.5895473957061768), ('Daumerlings Wanderschaft', 0.5864226818084717)]
Dokument Der Wolf und der Mensch [('Der Wolf und der Mensch', 0.6305369138717651), ('Daumerlings Wanderschaft', 0.572281002998352)]
Dokument Der Wolf und der Fuchs [('Nicht alle Tassen im Schrank haben', 0.5829917192459106), ('Partikelnliste der Rechtschreibreform von 1996', 0.5702115893363953)]
Dokument Der Fuchs und die Frau Gevatterin [('Die faule Spinnerin', 0.5855392217636108), ('Wuotis-Heer', 0.5775140523910522)]
Dokument Der Fuchs und die Katze [('Der Fuch

Dokument Die weiße und die schwarze Braut [('Die weiße und die schwarze Braut', 0.587993860244751), ('Der gastliche Kalbskopf', 0.5745494961738586)]
Dokument Der Eisenhans [('Schneewittchen (1959)', 0.6255795359611511), ('Liste deutscher Balladen', 0.6113294363021851)]
Dokument Die drei schwarzen Prinzessinnen [('Kuperan', 0.5767984390258789), ('Liste deutscher Balladen', 0.5751288533210754)]
Dokument Knoist und seine drei Söhne [('Knoist un sine dre Sühne', 0.5744149684906006), ('Piethan', 0.526465654373169)]
Dokument Das Mädchen von Brakel [('Dat Mäken von Brakel', 0.5883383750915527), ('Der Faule und der Fleißige', 0.5753101110458374)]
Dokument Das Hausgesinde [('Das Hausgesinde', 0.5663583278656006), ('Rabauke', 0.5289493799209595)]
Dokument Das Lämmchen und Fischchen [('Das Lämmchen und Fischchen', 0.6786699295043945), ('Die hagere Liese', 0.568756103515625)]
Dokument Simeliberg [('Simeliberg', 0.5410766005516052), ('Liste deutscher Balladen', 0.5402074456214905)]
Dokument Auf Rei

Dokument Die zwölf Apostel [('Liste deutscher Balladen', 0.5762494802474976), ('Gelobt sei Gott im höchsten Thron', 0.572190523147583)]
Dokument Die Rose [('Saterlied', 0.5668498277664185), ('Stimmloser palataler Frikativ', 0.5385435819625854)]
Dokument Armut und Demut führen zum Himmel [('Liste deutscher Balladen', 0.5823639035224915), ('Armut und Demut führen zum Himmel', 0.5672119855880737)]
Dokument Gottes Speise [('Gottes Speise', 0.6682755947113037), ('Die Kinder in Hungersnot', 0.6008444428443909)]
Dokument Die drei grünen Zweige [('Die drei grünen Zweige', 0.6004155874252319), ('Liste deutscher Balladen', 0.5675342679023743)]
Dokument Muttergottesgläschen [('Schnuppe', 0.5654966831207275), ('Ankaios (Sohn des Zeus)', 0.564538300037384)]
Dokument Das alte Mütterchen [('Liste deutscher Balladen', 0.5621724128723145), ('David Behme', 0.5505340695381165)]
Dokument Die himmlische Hochzeit [('Als du kamst zur Erde nieder', 0.5744894742965698), ('Am Weihnachtsbaum die Lichter brennen'

In [19]:
#unähnlichste Wikipedia Einträge zu den Märchen
most_disw=[]
for doc in range(len(wikivectors)):
    print("Dokument", df_titel.iloc[doc], model_wiki_dbow.docvecs.most_similar(negative=[wikivectors[doc]], topn=2)[0])
    most_disw.append(model_wiki_dbow.docvecs.most_similar(negative=[wikivectors[doc]])[0])

Dokument Der Froschkönig oder der eiserne Heinrich ('CMS', 0.0992421954870224)
Dokument Katze und Maus in Gesellschaft ('Sibongile Khumalo', 0.1116248071193695)
Dokument Marienkind ('New Britain (Connecticut)', 0.09380406141281128)
Dokument Von einem, der auszog, das Fürchten zu lernen ('Studio Tamassociati', 0.12583239376544952)
Dokument Der Wolf und die sieben jungen Geißlein ('Haager Akademie für Völkerrecht', 0.09668716043233871)
Dokument Der treue Johannes ('KMC', 0.10495851933956146)
Dokument Der gute Handel ('Liste der Biografien/Anf', 0.11568228900432587)
Dokument Der wunderliche Spielmann ('Liste von Zeittafeln', 0.10260332375764847)
Dokument Die zwölf Brüder ('Karin Putsch-Grassi', 0.10090206563472748)
Dokument Das Lumpengesindel ('Milutin Milankovic Medal', 0.11066578328609467)
Dokument Brüderchen und Schwesterchen ('Andrés Duany', 0.11563947796821594)
Dokument Rapunzel ('Andrés Duany', 0.10427423566579819)
Dokument Die drei Männlein im Walde ('ICP', 0.13762818276882172)
Dok

Dokument Der Dreschflegel vom Himmel ('MSU', 0.06355694681406021)
Dokument Die beiden Königskinder ('Liste der Richter am Internationalen Gerichtshof', 0.13198040425777435)
Dokument Vom klugen Schneiderlein ('Nelson Mandela Bay Metropolitan Municipality', 0.11093492060899734)
Dokument Die klare Sonne bringts an den Tag ('Vladimir Stevanović', 0.09310941398143768)
Dokument Das blaue Licht ('Andrés Duany', 0.11686327308416367)
Dokument Das eigensinnige Kind ('BEA', 0.015764381736516953)
Dokument Die drei Feldscherer ('Stadt San Marino', 0.08549969643354416)
Dokument Die sieben Schwaben ('Kunstschule', 0.12800967693328857)
Dokument Die drei Handwerksburschen ('ICP', 0.08395804464817047)
Dokument Der Königssohn, der sich vor nichts fürchtet ('Mitochondriales DNA-Depletionssyndrom', 0.10622049868106842)
Dokument Der Krautesel ('KMC', 0.09577283263206482)
Dokument Die Alte im Wald ('Samsic', 0.08297454565763474)
Dokument Die drei Brüder ('Cinven', 0.08650687336921692)
Dokument Der Teufel und

In [23]:
df_tempw = pd.DataFrame(columns=["Märchen"])
df_tempw["Märchen"] = titelw
df_tempw["ähnlichster Eintrag "] = most_simw
df_tempw["unähnlichster Eintrag"] = most_disw
df_tempw.to_csv("wiki_modelld2v_ähnlichedocs.csv")
df_tempw

Märchen  \
0        Der Froschkönig oder der eiserne Heinrich   
1                   Katze und Maus in Gesellschaft   
2                                       Marienkind   
3    Von einem, der auszog, das Fürchten zu lernen   
4          Der Wolf und die sieben jungen Geißlein   
..                                             ...   
218                                      Hans Dumm   
219                                       Blaubart   
220                                 Hurleburlebutz   
221                                     Der Okerlo   
222                           Prinzessin Mäusehaut   

                                  ähnlichster Eintrag   \
0                        (Kuperan, 0.6097391843795776)   
1                    (Bärenhunger, 0.5354288816452026)   
2       (Editha und die Hirschkuh, 0.5799908638000488)   
3    (Sagenweg Sagenhaftes Wölzertal, 0.60224759578...   
4            (Die faule Spinnerin, 0.5900070071220398)   
..                                                 ...   
218            (Ruine Baldenstein, 0.5474224090576172)   
219          (Die faule Spinnerin, 0.5792607069015503)   
220       (Rumpelstilzchen (1940), 0.5657806992530823)   
221                      (Kuperan, 0.6037895679473877)   
222                         (Itys, 0.5698932409286499)   

                                 unähnlichster Eintrag  
0                            (CMS, 0.0992421954870224)  
1              (Sibongile Khumalo, 0.1116248071193695)  
2     (New Britain (Connecticut), 0.09380406141281128)  
3           (Studio Tamassociati, 0.12583239376544952)  
4    (Haager Akademie für Völkerrecht, 0.0966871604...  
..                                                 ...  
218                         (IPD, 0.07717762887477875)  
219              (Monday Mornings, 0.0809209793806076)  
220           (Gefängnis Fresnes, 0.10542533546686172)  
221              (Forum of Firms, 0.10094840824604034)  
222            (Bernhard Furrer, 0.051886290311813354)  

[223 rows x 3 columns]

In [27]:
#Liste bestehend aus Liste erstellen, damit das in das Dataframe gepackt werden kann.
wcv = np.array(docvectors).tolist()
# zu Spalte in Dataframe hinzufügen
df["WikiVec"] = wcv



In [76]:
df["WikiVec"]=df["WikiVec"].apply(word_tokenize)
modified_w2v = [' '.join(i) for i in df["WikiVec"]]

In [77]:
from sklearn.metrics.pairwise import cosine_similarity 
dfw2v = pd.DataFrame(columns=["Märchen", "am ähnlichsten", "similarity%"])

for i in range(len(modified_w2v)):
    cosine_similarities = cosine_similarity(wikivectors[i:i+1], wikivectors).flatten()
    cosine_similarities = list(enumerate(cosine_similarities))
    cosine_similarities.pop(i)
    most_similar, similarity = max(cosine_similarities, key=lambda t:t[1])
    dfw2v.loc[len(dfw2v)] = [modified_w2v[i], modified_w2v[most_similar], similarity]
    
dfw2v["Märchen"] = df["Titel"]
dfw2v.to_csv("testi3.csv")
dfw2v

Märchen  \
0        Der Froschkönig oder der eiserne Heinrich   
1                   Katze und Maus in Gesellschaft   
2                                       Marienkind   
3    Von einem, der auszog, das Fürchten zu lernen   
4          Der Wolf und die sieben jungen Geißlein   
..                                             ...   
218                                      Hans Dumm   
219                                       Blaubart   
220                                 Hurleburlebutz   
221                                     Der Okerlo   
222                           Prinzessin Mäusehaut   

                                        am ähnlichsten  similarity%  
0    abends ging junger trommler ganz allein feld k...     0.732955  
1    zeiten schneider drei söhne einzige ziege zieg...     0.630917  
2    lebte alte königin gemahl schon lange jahre ge...     0.715611  
3    zeiten schneider drei söhne einzige ziege zieg...     0.747769  
4    arme witwe lebte einsam hüttchen hüttchen gart...     0.720576  
..                                                 ...          ...  
218  zwei brüder reicher armer reiche goldschmied b...     0.649712  
219  steinaltes mütterchen lebte herde gänse einöde...     0.712142  
220  zwei brüder reicher armer reiche goldschmied b...     0.712988  
221  junger jäger ging wald anstand frisches fröhli...     0.729978  
222  zwei brüder reicher armer reiche goldschmied b...     0.649761  

[223 rows x 3 columns]

In [80]:
df_temp2 = dfw2v.copy()
listew2v=df_temp2["am ähnlichsten"].tolist()

In [81]:
for x in range(len(listew2v)):
    listew2v[x] = listew2v[x][:20]
listew2v

['abends ging junger t',
 'zeiten schneider dre',
 'lebte alte königin g',
 'zeiten schneider dre',
 'arme witwe lebte ein',
 'königssohn gefiels m',
 'zeiten könig schönen',
 'zwei brüder reicher ',
 'arme witwe lebte ein',
 'berg tal begegnen ni',
 'steinaltes mütterche',
 'arme witwe lebte ein',
 'könig krank niemand ',
 'abends ging junger t',
 'frau drei töchter da',
 'zwei brüder reicher ',
 'steinaltes mütterche',
 'lande große klage wi',
 'mann frau einziges k',
 'zwei brüder reicher ',
 'steinaltes mütterche',
 'königssohn gefiels m',
 'zeiten schneider dre',
 'mann starb frau frau',
 'arme witwe lebte ein',
 'großen walde wohnte ',
 'vater zwei söhne dav',
 'zwei brüder reicher ',
 'zwei brüder reicher ',
 'alte geiß sieben jun',
 'brüderchen nahm schw',
 'großen walde wohnte ',
 'junger jäger ging wa',
 'dorfe lebte mann fra',
 'meister pfriem klein',
 'abends ging junger t',
 'bauersmann sohn groß',
 'zwei brüder reicher ',
 'schneider sohn klein',
 'walde lebte mann dre',


In [82]:
for s in range (len(listew2v)):
    simon = listew2v[s]
    simon = simski.get(simon)
    listew2v[s] = simon
listew2v

['Der Trommler',
 'Tischchen deck dich, Goldesel und Knüppel aus dem Sack',
 'Die Gänsemagd',
 'Tischchen deck dich, Goldesel und Knüppel aus dem Sack',
 'Schneeweißchen und Rosenrot',
 'Der Königssohn, der sich vor nichts fürchtet',
 'Der goldene Vogel',
 'Die zwei Brüder',
 'Schneeweißchen und Rosenrot',
 'Die beiden Wanderer',
 'Die Gänsehirtin am Brunnen',
 'Schneeweißchen und Rosenrot',
 'Das Wasser des Lebens',
 'Der Trommler',
 'Einäuglein, Zweiäuglein und Dreiäuglein',
 'Die zwei Brüder',
 'Die Gänsehirtin am Brunnen',
 'Der singende Knochen',
 'Der starke Hans',
 'Die zwei Brüder',
 'Die Gänsehirtin am Brunnen',
 'Der Königssohn, der sich vor nichts fürchtet',
 'Tischchen deck dich, Goldesel und Knüppel aus dem Sack',
 'Die drei Männlein im Walde',
 'Schneeweißchen und Rosenrot',
 'Hänsel und Gretel',
 'Von einem, der auszog, das Fürchten zu lernen',
 'Die zwei Brüder',
 'Die zwei Brüder',
 'Der Wolf und die sieben jungen Geißlein',
 'Brüderchen und Schwesterchen',
 'Hänsel un

In [83]:
dfw2v["am ähnlichsten"]=listew2v
dfw2v["Märchen"]=df["Titel"]
dfw2v.to_csv("wiki_doc2vec_kosinus.csv")
dfw2v

Märchen  \
0        Der Froschkönig oder der eiserne Heinrich   
1                   Katze und Maus in Gesellschaft   
2                                       Marienkind   
3    Von einem, der auszog, das Fürchten zu lernen   
4          Der Wolf und die sieben jungen Geißlein   
..                                             ...   
218                                      Hans Dumm   
219                                       Blaubart   
220                                 Hurleburlebutz   
221                                     Der Okerlo   
222                           Prinzessin Mäusehaut   

                                        am ähnlichsten  similarity%  
0                                         Der Trommler     0.732955  
1    Tischchen deck dich, Goldesel und Knüppel aus ...     0.630917  
2                                        Die Gänsemagd     0.715611  
3    Tischchen deck dich, Goldesel und Knüppel aus ...     0.747769  
4                          Schneeweißchen und Rosenrot     0.720576  
..                                                 ...          ...  
218                                    Die zwei Brüder     0.649712  
219                         Die Gänsehirtin am Brunnen     0.712142  
220                                    Die zwei Brüder     0.712988  
221                                      Der Krautesel     0.729978  
222                                    Die zwei Brüder     0.649761  

[223 rows x 3 columns]

In [103]:
model_wiki_dbow.docvecs.most_similar(positive=["Ostern"], topn=10)

[('Gründonnerstag', 0.6605018377304077),
 ('Weihnachten', 0.6575650572776794),
 ('Advent', 0.6213794350624084),
 ('Ostersamstag', 0.6159977912902832),
 ('Heilige Drei Könige', 0.6111978888511658),
 ('Osternacht', 0.609670102596283),
 ('Karwoche', 0.6079638004302979),
 ('Weihnachten weltweit', 0.6036931276321411),
 ('Engelamt', 0.5967838764190674),
 ('Ostersonntag', 0.5949702858924866)]

In [3]:
vec = [model_wiki_dbow.docvecs["Pablo Picasso"] - model_wiki_dbow.docvecs["Spanien"] + model_wiki_dbow.docvecs["Frankreich"]]
model_wiki_dbow.docvecs.most_similar(vec, topn=20)

[('Pablo Picasso', 0.7748591899871826),
 ('Henri Matisse', 0.7009071111679077),
 ('Max Ernst', 0.6492255330085754),
 ('Paul Cézanne', 0.6484525203704834),
 ('Alberto Giacometti', 0.6461941003799438),
 ('Kubismus', 0.630496621131897),
 ('Paul Klee', 0.6304214596748352),
 ('André Derain', 0.6272828578948975),
 ('Joan Miró', 0.6142573356628418),
 ('Amedeo Modigliani', 0.6072903871536255),
 ('Max Beckmann', 0.6051748991012573),
 ('Marc Chagall', 0.6050670146942139),
 ('Marcel Duchamp', 0.6045782566070557),
 ('Wols', 0.6029481887817383),
 ('Edgar Degas', 0.6020801663398743),
 ('Claude Monet', 0.5961887836456299),
 ('Man Ray', 0.5896604061126709),
 ('Fauvismus', 0.5852196216583252),
 ('Constantin Brâncuși', 0.5796884298324585),
 ('Piet Mondrian', 0.5780773162841797)]

In [55]:
model_dbow.docvecs.most_similar([docvectors[216]], topn=10)

[(216, 0.9789676070213318),
 (53, 0.8415557742118835),
 (141, 0.628270149230957),
 (137, 0.6004363298416138),
 (69, 0.5579290986061096),
 (27, 0.5350401997566223),
 (202, 0.5130857825279236),
 (61, 0.5128813982009888),
 (63, 0.5027901530265808),
 (160, 0.4944307208061218)]

In [56]:
#Der Ranzen, das Hütlein und das Hörnlein erst an Stelle 7
model_wiki_dbow.docvecs.most_similar([wikivectors[216]], topn=10)

[('Von dem Schneider, der bald reich wurde', 0.5582196116447449),
 ('Herr Fix und Fertig', 0.5492034554481506),
 ('Die faule Spinnerin', 0.5428133606910706),
 ('Der König der Raben', 0.5423762798309326),
 ('Rumpelstilzchen (1940)', 0.5387989282608032),
 ('De wilde Mann', 0.5358288288116455),
 ('Der Ranzen, das Hütlein und das Hörnlein', 0.5243985652923584),
 ('Die lange Nase', 0.5227905511856079),
 ('Der Faule und der Fleißige', 0.5213949680328369),
 ('Daumerlings Wanderschaft', 0.516858696937561)]

# Wurden zu den Märchen jeweils dieselben Märchen als das Ähnlichste berechnet?

In [2]:
tfidfk = pd.read_csv("tfidf_kosinus.csv") 
doc2veck = pd.read_csv("doc2vec_kosinus.csv") 
wiki2veck = pd.read_csv("wiki_doc2vec_kosinus.csv") 


In [3]:
df_kosinus = pd.DataFrame(columns=["tfidf", "doc2vec", "wiki_doc2vec"])
df_kosinus["tfidf"] = tfidfk["am ähnlichsten"]
df_kosinus["doc2vec"] = doc2veck["am ähnlichsten"]
df_kosinus["wiki_doc2vec"] = wiki2veck["am ähnlichsten"]
df_kosinus

tfidf                 doc2vec  \
0              Der Eisenhans          Die Brautschau   
1    Der Fuchs und die Katze           Der süße Brei   
2     Das Mädchen ohne Hände       Die zwölf Apostel   
3            Die zwei Brüder         Die drei Faulen   
4     Der Wolf und der Fuchs  Der Wolf und der Fuchs   
..                       ...                     ...   
218          Der starke Hans           Hans heiratet   
219         Die zwölf Brüder   Die drei Spinnerinnen   
220        Der goldene Vogel           Häsichenbraut   
221       Der liebste Roland           Rätselmärchen   
222  Die kluge Bauerntochter         Die zwölf Jäger   

                                          wiki_doc2vec  
0                                         Der Trommler  
1    Tischchen deck dich, Goldesel und Knüppel aus ...  
2                                        Die Gänsemagd  
3    Tischchen deck dich, Goldesel und Knüppel aus ...  
4                          Schneeweißchen und Rosenrot  
..                                                 ...  
218                                    Die zwei Brüder  
219                         Die Gänsehirtin am Brunnen  
220                                    Die zwei Brüder  
221                                      Der Krautesel  
222                                    Die zwei Brüder  

[223 rows x 3 columns]

In [4]:
df_kosinus['gleiches Märchen'] = (df_kosinus["tfidf"] == df_kosinus["doc2vec"]) & (df_kosinus["tfidf"] == df_kosinus["wiki_doc2vec"])
df_kosinus
df_kosinus.to_csv("gleiche_Märchen_ausgewählt.csv")

### Visualisierung

In [20]:
import texthero as hero
df["tsne"] = docvectors
df["tsnewiki"] = wikivectors
df["tsnetfidf"] = np.array(tf_idf).tolist()


# t-sne algorithmus für die Vektoren
# Vektor Doc2Vec
df["tsne"] = hero.tsne(df["tsne"])
df["tsnewiki"] = hero.tsne(df["tsnewiki"])
df["tsnetfidf"] = hero.tsne(df["tsnetfidf"])


In [24]:
#Scatter plot für die Vektoren
hero.scatterplot(df, col="tsne", title="Doc2Vec PV DBOW Visualisierung mit T-SNE", hover_data = ["Titel"], color = erscheinung)
hero.scatterplot(df, col="tsnetfidf", title="TFIDF Visualisierung mit T-SNE", hover_data = ["Titel"], color = erscheinung)
hero.scatterplot(df, col="tsnewiki", title="Doc2Vec Wiki PV DBOW Visualisierung mit T-SNE", hover_data = ["Titel"], color = erscheinung)

